In [ ]:
!pip install --quiet -qqq --upgrade accelerate peft bitsandbytes transformers trl faiss-gpu langchain_community wandb flash-attn
# flash-attn

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.4/44.4 kB 1.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.6/2.6 MB 27.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.4/50.4 kB 3.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 322.5/322.5 kB 20.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 122.4/122.4 MB 7.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.9/9.9 MB 62.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 318.4/318.4 kB 19.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.5/85.5 MB 8.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.4/2.4 MB 57.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.0/13.0 MB 73.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.3/207.3 kB 16.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 45.4 MB/s eta 0:00:00
   ━━━━━━

In [ ]:
# load the required packages.
import torch
from datasets import load_dataset, Dataset
from peft import LoraConfig, AutoPeftModelForCausalLM
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig, TrainingArguments, AutoConfig, set_seed
from trl import SFTTrainer
import os
import transformers
import numpy as np
import pandas as pd
from peft import LoraConfig, AutoPeftModelForCausalLM, PeftModel, get_peft_model
import sqlparse
import bitsandbytes as bnb
import os
from huggingface_hub import hf_hub_download
from huggingface_hub import HfFileSystem
import re
import json

In [ ]:
# from google.colab import drive
# from google.colab import userdata
# drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
#transformers.logging.set_verbosity_info()

In [ ]:
WRITE_TOKEN = userdata.get('hf_write')
READ_TOKEN = userdata.get('hf_read')

In [ ]:
model_name = "meta-llama/Llama-3.2-1B-Instruct"
out_name = "lleticiasilvaa/Llama-3.2-1B-Instruct-SchemaLinking-v1"
prev_checkpoint = "checkpoint-3000"

In [ ]:
#!huggingface-cli login

In [ ]:
bird_id="NESPED-GEN/bird"
spider_id="NESPED-GEN/spider"

selector_id = "NESPED-GEN/selector_testes"

### Load Data


In [ ]:
# bird = load_dataset(bird_id, split="train").to_pandas()
# spider = load_dataset(spider_id, split="train").to_pandas()

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/899 [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/2.85M [00:00<?, ?B/s]

retry_train-00000-of-00001.parquet:   0%|          | 0.00/1.92M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/9428 [00:00<?, ? examples/s]

...

Generating train split:   0%|          | 0/8656 [00:00<?, ? examples/s]

Generating dev split:   0%|          | 0/1034 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/2147 [00:00<?, ? examples/s]

Generating train_spider split:   0%|          | 0/6997 [00:00<?, ? examples/s]

Generating train_others split:   0%|          | 0/1659 [00:00<?, ? examples/s]

In [ ]:
# df = pd.concat([spider, bird], axis=0)
# df = df.fillna('')

In [ ]:
# df.reset_index(drop=True, inplace=True)

In [ ]:
df = load_dataset(selector_id, split="trainSpider").to_pandas()

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/1.23k [00:00<?, ?B/s]

trainSpider-00000-of-00001.parquet:   0%|          | 0.00/2.00M [00:00<?, ?B/s]

devSpider-00000-of-00001.parquet:   0%|          | 0.00/297k [00:00<?, ?B/s]

testSpider-00000-of-00001.parquet:   0%|          | 0.00/649k [00:00<?, ?B/s]

Generating trainSpider split:   0%|          | 0/8656 [00:00<?, ? examples/s]

Generating devSpider split:   0%|          | 0/1034 [00:00<?, ? examples/s]

Generating testSpider split:   0%|          | 0/2147 [00:00<?, ? examples/s]

# Load Base Model

In [ ]:
def download_checkpoint(adapter_model_id, checkpoint):


    fs = HfFileSystem()
    for file in fs.ls(f'{adapter_model_id}/{checkpoint}', detail=False):
        file_name = file.split(checkpoint)[-1]

        hf_hub_download(repo_id=adapter_model_id, filename=(f'{checkpoint}{file_name}'), local_dir='out')

    for file in fs.ls(f'{adapter_model_id}/logs', detail=False):
        file_name = file.split(checkpoint)[-1]

        hf_hub_download(repo_id=adapter_model_id, filename=(f'logs/{file_name.split("/")[-1]}'), local_dir='out')

In [ ]:
# download_checkpoint(out_name, prev_checkpoint)

In [ ]:


seed=14

if (prev_checkpoint != None):
    try:
        download_checkpoint(out_name, prev_checkpoint)
    except:
        pass
tokenizer = AutoTokenizer.from_pretrained(model_name, trust_remote_code=True, token=READ_TOKEN, map_device="auto", add_eos_token=True, use_fast=True)

if torch.cuda.is_bf16_supported():
  compute_dtype = torch.bfloat16
  attn_implementation = 'flash_attention_2'
else:
  compute_dtype = torch.float16
  attn_implementation = 'sdpa'

tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right"


bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    # load_in_8bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=compute_dtype,
    bnb_4bit_use_double_quant=False,
)

model = AutoModelForCausalLM.from_pretrained(
    model_name,
    torch_dtype=compute_dtype,
    device_map="auto",
    quantization_config=bnb_config,

    trust_remote_code=True,
    token=READ_TOKEN,
    # attn_implementation=attn_implementation
)

# model.resize_token_embeddings(max(len(tokenizer), model.config.vocab_size))

checkpoint-3000/README.md:   0%|          | 0.00/5.11k [00:00<?, ?B/s]

checkpoint-3000/adapter_config.json:   0%|          | 0.00/838 [00:00<?, ?B/s]

adapter_model.safetensors:   0%|          | 0.00/180M [00:00<?, ?B/s]

optimizer.pt:   0%|          | 0.00/92.4M [00:00<?, ?B/s]

rng_state.pth:   0%|          | 0.00/14.3k [00:00<?, ?B/s]

...

tokenizer.json:   0%|          | 0.00/9.09M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/296 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/877 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/2.47G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/189 [00:00<?, ?B/s]

#### Chat Template

In [ ]:
def to_sql(query):
  return sqlparse.format(query, reindent=True, keyword_case='upper')

def replace_last_sql_content(text, new_content):
    matches = list(re.finditer(r'```sql (.*?)```', text, re.DOTALL))
    if not matches:
        return text

    last_match = matches[-1]

    start, end = last_match.span(1)
    return text[:start] + new_content + text[end:]

# def apply_template(row, tokenizer=tokenizer, n_examplea=0):
#     question = row['question_en']
#     schema = row['schema_llm']
#     sql = to_sql(row['query_llm'])

#     system = "Given a user question and the schema of a database, your task is to generate an SQL query that accurately answers the question based on the provided schema."


#     chat = [{'role': 'user', 'content': f"# System:\n{system}\n\n# Schema:\n```sql\n{schema}\n```\n\n# Question: {question}"},
#             {'role': 'assistant', 'content': f"```sql\n{sql}\n```"}
#             ]

#     row['text'] = tokenizer.apply_chat_template(chat, tokenize=False, add_generation_prompt=False)

#     return row

def apply_template(row, tokenizer=tokenizer, n_examplea=0):
    question = row['question_en']
    schema = row['schema_llm_t']
    schema_linking = to_sql(row['selector_correct'])

    system = "Given a user question and the schema of a database, your task is to generate an JSON with the the names of tables and columns of the schema that the question is referring to."

    chat = [{'role': 'user', 'content': f"# System:\n{system}\n\n# Schema:\n```sql\n{schema}\n```\n\n# Question: {question}"},
            {'role': 'assistant', 'content': f"```json\n{schema_linking}\n```"}
            ]

    row['text'] = tokenizer.apply_chat_template(chat, tokenize=False, add_generation_prompt=False)

    return row

In [ ]:
# spider_chain = json.load(open("/content/drive/Shareddrives/LLMs/Datasets/spider/spider_chain.json", "r"))
# bird_chain = json.load(open("/content/drive/Shareddrives/LLMs/Datasets/bird/bird_chain.json", "r"))

In [ ]:
# df['chain'] = spider_chain + bird_chain

In [ ]:
df = df.apply(apply_template, axis=1)

In [ ]:
df.head()

db_id                                             schema  \
0  department_management  \nCREATE TABLE department (\n\t"Department_ID"...   
1  department_management  \nCREATE TABLE department (\n\t"Department_ID"...   
2  department_management  \nCREATE TABLE department (\n\t"Department_ID"...   
3  department_management  \nCREATE TABLE department (\n\t"Department_ID"...   
4  department_management  \nCREATE TABLE department (\n\t"Department_ID"...   

                                         question_en hardness  \
0  How many heads of the departments are older th...     easy   
1  List the name, born state and age of the heads...   medium   
2  List the creation year, name and budget of eac...   medium   
3  What are the maximum and minimum budget of the...   medium   
4  What is the average number of employees of the...     easy   

                                          schema_llm  \
0  Table department (\n    department.Department_...   
1  Table department (\n    department.Department_...   
2  Table department (\n    department.Department_...   
3  Table department (\n    department.Department_...   
4  Table department (\n    department.Department_...   

                                           query_llm  \
0         SELECT count(*) FROM head WHERE age  >  56   
1  SELECT name ,  born_state ,  age FROM head ORD...   
2  SELECT creation ,  name ,  budget_in_billions ...   
3  SELECT max(budget_in_billions) ,  min(budget_i...   
4  SELECT avg(num_employees) FROM department WHER...   

                                            selector  \
0                 {\n  'head': ['head_id', 'age']\n}   
1  {\n  'head': ['head_id', 'name', 'born_state',...   
2  {\n  'department': ['department_id', 'name', '...   
3  {\n  'department': ['department_id', 'budget_i...   
4  {\n  'department': ['department_id', 'ranking'...   

                                       schema_llm_ct  \
0  CREATE TABLE department (\n    department.Depa...   
1  CREATE TABLE department (\n    department.Depa...   
2  CREATE TABLE department (\n    department.Depa...   
3  CREATE TABLE department (\n    department.Depa...   
4  CREATE TABLE department (\n    department.Depa...   

                              schema_llm_columns_min  \
0  Table department (\n    department.department_...   
1  Table department (\n    department.department_...   
2  Table department (\n    department.department_...   
3  Table department (\n    department.department_...   
4  Table department (\n    department.department_...   

                           schema_llm_columns_min_ct  \
0  CREATE TABLE department (\n    department.depa...   
1  CREATE TABLE department (\n    department.depa...   
2  CREATE TABLE department (\n    department.depa...   
3  CREATE TABLE department (\n    department.depa...   
4  CREATE TABLE department (\n    department.depa...   

                                  schema_llm_all_min  \
0  Table department (\n    department.department_...   
1  Table department (\n    department.department_...   
2  Table department (\n    department.department_...   
3  Table department (\n    department.department_...   
4  Table department (\n    department.department_...   

                               schema_llm_all_min_ct  \
0  CREATE TABLE department (\n    department.depa...   
1  CREATE TABLE department (\n    department.depa...   
2  CREATE TABLE department (\n    department.depa...   
3  CREATE TABLE department (\n    department.depa...   
4  CREATE TABLE department (\n    department.depa...   

                                         schema_dict  \
0  {\n  'department': ['Department_ID', 'Name', '...   
1  {\n  'department': ['Department_ID', 'Name', '...   
2  {\n  'department': ['Department_ID', 'Name', '...   
3  {\n  'department': ['Department_ID', 'Name', '...   
4  {\n  'department': ['Department_ID', 'Name', '...   

                                    selector_correct  \
0                 {\n  'head': ['head_ID', 'age']\n}   
1  {\n  

In [ ]:
# df['n_tokens'] = df['text'].apply(lambda x: len(tokenizer.encode(x)))

In [ ]:
# import seaborn as sns
# sns.histplot(df['n_tokens'])

In [ ]:
print(df['text'][df.index[50]])

<|begin_of_text|><|start_header_id|>system<|end_header_id|>

Cutting Knowledge Date: December 2023
Today Date: 06 Oct 2024

<|eot_id|><|start_header_id|>user<|end_header_id|>

# System:
Given a user question and the schema of a database, your task is to generate an JSON with the the names of tables and columns of the schema that the question is referring to.

# Schema:
```sql
TABLE city (
    city.City_ID (INT),
    city.Official_Name (TEXT),
    city.Status (TEXT),
    city.Area_km_2 (REAL),
    city.Population (REAL),
    city.Census_Ranking (TEXT),
)

TABLE competition_record (
    competition_record.Competition_ID (INT),
    competition_record.Farm_ID (INT),
    competition_record.Rank (INT),
)

TABLE farm (
    farm.Farm_ID (INT),
    farm.Year (INT),
    farm.Total_Horses (REAL),
    farm.Working_Horses (REAL),
    farm.Total_Cattle (REAL),
    farm.Oxen (REAL),
    farm.Bulls (REAL),
    farm.Cows (REAL),
    farm.Pigs (REAL),
    farm.Sheep_and_Goats (REAL),
)

TABLE farm_compe

In [ ]:
_df = pd.DataFrame(columns=['text'])
_df['text'] = df.sample(frac=1, random_state=14).reset_index(drop=True)['text']
_df = Dataset.from_pandas(_df)
_df = _df.train_test_split(test_size=0.01, shuffle=True, seed=14)
train_dataset, valid_dataset = _df["train"], _df["test"]

### Finetuning

In [ ]:
from huggingface_hub import login, create_repo
from google.colab import userdata
import wandb
import os

token = userdata.get('hf_write')
login(token=token)
set_seed(1234)


The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: write).
Your token has been saved to /root/.cache/huggingface/token
Login successful


In [ ]:
def find_all_linear_names(model, new_tokens=False):
    lora_module_names = set()
    for name, module in model.named_modules():
        if isinstance(module, bnb.nn.Linear4bit) or isinstance(module, bnb.nn.Linear8bitLt):
            names = name.split(".")
            lora_module_names.add(names[0] if len(names) == 1 else names[-1])
    if(new_tokens):
      lora_module_names.add("lm_head")
    return list(lora_module_names)

In [ ]:
modules = find_all_linear_names(model)
print(f"Found {len(modules)} modules to quantize: {modules}")

Found 7 modules to quantize: ['v_proj', 'k_proj', 'down_proj', 'o_proj', 'q_proj', 'up_proj', 'gate_proj']


In [ ]:
peft_config = LoraConfig(
    lora_alpha=128,
    lora_dropout=0.1,
    r=64,
    target_modules=modules,
    # modules_to_save=["embed_tokens"],
)

In [ ]:
torch.cuda.empty_cache()

In [ ]:
steps=250
strategy="steps"

trainer = SFTTrainer(
    model= model,
    tokenizer=tokenizer,

    train_dataset=train_dataset,
    eval_dataset=valid_dataset,

    peft_config=peft_config,

    dataset_text_field="text",
    max_seq_length=2048,
    args= TrainingArguments(
      output_dir="out",

      save_strategy=strategy,
      save_steps= steps,

      logging_strategy=strategy,
      logging_steps=steps,
      logging_dir="out/logs",

      eval_strategy=strategy,
      eval_steps=steps,

      num_train_epochs=5,
      per_device_train_batch_size=1,
      per_device_eval_batch_size=1,
      gradient_accumulation_steps=8,
      gradient_checkpointing=True,
      fp16=True,
      bf16=False,

      optim="paged_adamw_8bit",
      learning_rate=1e-4,
      weight_decay=0.001,
      max_grad_norm=0.3,
      max_steps=-1,
      warmup_ratio=0.03,
      group_by_length=True,
      lr_scheduler_type="cosine",
      seed= seed,


      report_to=["tensorboard"],
      push_to_hub=True,
      hub_strategy="all_checkpoints",
      hub_model_id=out_name,

      label_names=["labels"]
  )

)
if(prev_checkpoint != None):
    trainer.train(f"out/{prev_checkpoint}")
else:
    trainer.train()

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:100: FutureWarning: Deprecated argument(s) used in '__init__': dataset_text_field, max_seq_length. Will not be supported from version '1.0.0'.

Deprecated positional argument(s) used in SFTTrainer, please use the SFTConfig to set these arguments instead.
  warnings.warn(message, FutureWarning)
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:283: UserWarning: You passed a `max_seq_length` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:321: UserWarning: You passed a `dataset_text_field` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(


Map:   0%|          | 0/8569 [00:00<?, ? examples/s]

Map:   0%|          | 0/87 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)
/usr/local/lib/python3.10/dist-packages/transformers/trainer.py:3262: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend yo

/usr/local/lib/python3.10/dist-packages/torch/_dynamo/eval_frame.py:600: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.4 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)
/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:295: FutureWarning: `torch.cpu.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cpu', args...)` instead.
  with torch.enable_grad(), device_autocast_ctx, torch.cpu.amp.autocast(**ctx.cpu_autocast_kwargs):  # type: ignore[attr-defined]
/usr/local/lib/python3.10/dist-packages/torch/_dynamo/eval_frame.py:600: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.4 we will raise an except

In [ ]:
trainer.push_to_hub()

CommitInfo(commit_url='https://huggingface.co/lleticiasilvaa/Llama-3.2-1B-Instruct-SchemaLinking-v1/commit/3c39d6fe35ee293b98d49fa0cbc2cf7d1c498844', commit_message='End of training', commit_description='', oid='3c39d6fe35ee293b98d49fa0cbc2cf7d1c498844', pr_url=None, pr_revision=None, pr_num=None)